In [1]:
import pandas as pd
import numpy as np
import os
import graphlab as gl
import graphlab.aggregate as agg
import math
from graphlab import SFrame
from sklearn.metrics import confusion_matrix
from sklearn.metrics import roc_auc_score
from sklearn.metrics import roc_curve, auc
import matplotlib as plt

In [2]:
###df=pd.read_excel('Online Retail.xlsx')
###df.info()
###df['CustomerID']=df.CustomerID.astype(object)
###df.dropna()
###len(df)

In [3]:
###import sys
###reload(sys)
###sys.setdefaultencoding('utf8')
###df.to_csv('Online Retail.csv')

In [4]:
gl.canvas.set_target('ipynb')

In [5]:
sf=gl.SFrame.read_csv('Online Retail.csv')
len(sf)

This non-commercial license of GraphLab Create for academic use is assigned to patelsumitm@gmail.com and will expire on February 23, 2019.


[INFO] graphlab.cython.cy_server: GraphLab Create v2.1 started. Logging: C:\Users\Timus\AppData\Local\Temp\graphlab_server_1522656741.log.0


Finished parsing file C:\Users\Timus\Projects\Recommendation System for Wholesale Customers\Online Retail.csv

Parsing completed. Parsed 100 lines in 0.566255 secs.

------------------------------------------------------
Inferred types from first 100 line(s) of file as 
column_type_hints=[long,long,str,str,long,str,float,float,str]
If parsing fails due to incorrect types, you can correct
the inferred type list above and pass it to read_csv in
the column_type_hints argument
------------------------------------------------------


...

Unable to parse line "311394,C564279,23064,CINDERELLA CHANDELIER ,-3,2011-08-24 10:54:00,49.95,17706.0,United Kingdom"

9291 lines failed to parse correctly

Finished parsing file C:\Users\Timus\Projects\Recommendation System for Wholesale Customers\Online Retail.csv

Parsing completed. Parsed 532618 lines in 0.709565 secs.

532618

In [6]:
sf.dtype()

[int, int, str, str, int, str, float, float, str]

In [7]:
sf['CustomerID']=sf['CustomerID'].astype(int)
sf['Description']=sf['Description'].astype(str)
sf['Items'] = sf['StockCode']+':'+sf['Description']
sf.dropna()
len(sf)

532618

In [8]:
sf=sf[['CustomerID','Items','Quantity']]
sf

Columns:
	CustomerID	int
	Items	str
	Quantity	int

Rows: 532618

Data:
+------------+-------------------------------+----------+
| CustomerID |             Items             | Quantity |
+------------+-------------------------------+----------+
|   17850    | 85123A:WHITE HANGING HEART... |    6     |
|   17850    |   71053:WHITE METAL LANTERN   |    6     |
|   17850    | 84406B:CREAM CUPID HEARTS ... |    8     |
|   17850    | 84029G:KNITTED UNION FLAG ... |    6     |
|   17850    | 84029E:RED WOOLLY HOTTIE W... |    6     |
|   17850    | 22752:SET 7 BABUSHKA NESTI... |    2     |
|   17850    | 21730:GLASS STAR FROSTED T... |    6     |
|   17850    |  22633:HAND WARMER UNION JACK |    6     |
|   17850    | 22632:HAND WARMER RED POLK... |    6     |
|   13047    | 84879:ASSORTED COLOUR BIRD... |    32    |
+------------+-------------------------------+----------+
[532618 rows x 3 columns]
Note: Only the head of the SFrame is printed.
You can use print_rows(num_rows=m, num_columns=n) to print more rows and columns.

In [9]:
data=sf.groupby(['CustomerID', 'Items'],operations={'totalquantity': agg.SUM('Quantity'), 'meanquantity': agg.AVG('Quantity'), 'stdquantity': agg.STD('Quantity')})
data['meanquantity']=data['meanquantity'].astype(int)
data['stdquantity']=data['stdquantity'].astype(int)

In [10]:
users= data['CustomerID'].unique()
users.show()
items= data['Items'].unique()
items.show()

In [11]:
data

Columns:
	CustomerID	int
	Items	str
	meanquantity	int
	totalquantity	int
	stdquantity	int

Rows: 273425

Data:
+------------+--------------------------------+--------------+---------------+-------------+
| CustomerID |             Items              | meanquantity | totalquantity | stdquantity |
+------------+--------------------------------+--------------+---------------+-------------+
|   16556    |   22982:PANTRY PASTRY BRUSH    |      12      |       12      |      0      |
|   12857    |    21272:SALLE DE BAIN HOOK    |      12      |       12      |      0      |
|   12476    | 23052:RECYCLED ACAPULCO MA...  |      2       |       2       |      0      |
|   16022    |  22660:DOORMAT I LOVE LONDON   |      1       |       1       |      0      |
|   16170    | 22570:FELTCRAFT CUSHION RABBIT |      8       |       8       |      0      |
|   12444    | 23171:REGENCY TEA PLATE GREEN  |      12      |       12      |      0      |
|   16906    |   82580:BATHROOM METAL SIGN    |      1       |       3       |      0      |
|    None    | 23209:LUNCH BAG VINTAGE DOILY  |      1       |      110      |      1      |
|   17120    | 84946:ANTIQUE SILVER T-LIG...  |      12      |       12      |      0      |
|   13458    |     22712:CARD DOLLY GIRL      |      12      |       12      |      0      |
+------------+--------------------------------+--------------+---------------+-------------+
[273425 rows x 5 columns]
Note: Only the head of the SFrame is printed.
You can use print_rows(num_rows=m, num_columns=n) to print more rows and columns.

In [12]:
m=gl.recommender.create(data, user_id='CustomerID', item_id='Items', target='totalquantity')
m.show()

Recsys training: model = ranking_factorization_recommender

Preparing data set.

Data has 273425 observations with 4340 users and 5732 items.

Data prepared in: 0.352555s

Training ranking_factorization_recommender for recommendations.

...

+---------+--------------+-------------------+-----------------------+-------------+

Optimization Complete: Maximum number of passes through the data reached (hard limit).

Computing final objective value and training RMSE.

Final objective value: 98474.4

Final training RMSE: 186.406

In [13]:
m.evaluate_rmse(dataset=data, target='totalquantity')

{'rmse_by_item': Columns:
 	Items	str
 	count	int
 	rmse	float
 
 Rows: 5732
 
 Data:
 +--------------------------------+-------+---------------+
 |             Items              | count |      rmse     |
 +--------------------------------+-------+---------------+
 | 23249:VINTAGE RED ENAMEL T...  |   57  | 22.2001028581 |
 |   22695:WICKER WREATH SMALL    |   83  | 15.7801836077 |
 |            84873A:             |   1   | 59.3537178768 |
 | 84947:ANTIQUE SILVER TEA G...  |  178  | 116.306478258 |
 | 47566B:reverse previous ad...  |   1   | 1127.60119512 |
 | 22931:BAKING MOULD HEART W...  |   96  | 20.2454457801 |
 |             21432:             |   1   | 48.9694053489 |
 | 37464:ROBOT MUG IN DISPLAY BOX |   2   |  69.572266879 |
 |             21332:             |   1   | 12.2640106523 |
 | 84857C:PINK MONTE CARLO HA...  |   9   | 22.5538865414 |
 +--------------------------------+-------+---------------+
 [5732 rows x 3 columns]
 Note: Only the head of the SFrame is printed.
 Y

In [14]:
recs=m.recommend(users,k=20)

recommendations finished on 1000/4340 queries. users per second: 6747.91

recommendations finished on 2000/4340 queries. users per second: 6747.82

recommendations finished on 3000/4340 queries. users per second: 7000.06

recommendations finished on 4000/4340 queries. users per second: 6983.7

In [15]:
high_rated_data = data[data["totalquantity"] >= 1]
low_rated_data = data[data["totalquantity"] < 1]
train_data_1, test = gl.recommender.util.random_split_by_user(high_rated_data, user_id='CustomerID', item_id='Items')
train = train_data_1.append(low_rated_data)

In [16]:
recommender = gl.recommender.create(train, user_id='CustomerID', item_id='Items', target='totalquantity')

factorization = gl.recommender.factorization_recommender.create(train,user_id='CustomerID',item_id='Items',target='totalquantity',solver='als')

rfactorization= gl.recommender.ranking_factorization_recommender.create(train,target='totalquantity',user_id='CustomerID',item_id='Items')

popularity=gl.recommender.popularity_recommender.create(train,user_id='CustomerID',item_id='Items',target='totalquantity')

itemsimilarity=gl.recommender.item_similarity_recommender.create(train,user_id='CustomerID',item_id='Items',target='totalquantity',similarity_type='pearson')

Recsys training: model = ranking_factorization_recommender

Preparing data set.

Data has 260212 observations with 4338 users and 5725 items.

Data prepared in: 0.260373s

Training ranking_factorization_recommender for recommendations.

...

| 1.04s                               | 100              | 5725            |

+-------------------------------------+------------------+-----------------+

Finalizing lookup tables.

Generating candidate set for working with new users.

Finished training in 1.0534s

In [17]:
print('recommender rmse=', recommender.evaluate_rmse(dataset=data,target='totalquantity'))

print('factorization rmse=', factorization.evaluate_rmse(dataset=data,target='totalquantity'))

print('ranking factoriaztion rmse=', rfactorization.evaluate_rmse(dataset=data,target='totalquantity'))

print('popularity rmse=', popularity.evaluate_rmse(dataset=data,target='totalquantity'))

print('item similarity rmse=', itemsimilarity.evaluate_rmse(dataset=data,target='totalquantity'))

('recommender rmse=', {'rmse_by_user': Columns:
	CustomerID	int
	count	int
	rmse	float

Rows: 4340

Data:
+------------+-------+---------------+
| CustomerID | count |      rmse     |
+------------+-------+---------------+
|   14515    |   69  | 68.3318435511 |
|   14406    |   8   | 19.7784608756 |
|   17338    |  390  | 103.829543105 |
|   15615    |  187  | 101.637222133 |
|   17325    |   6   | 15.5998947329 |
|   16284    |   87  | 55.8871656248 |
|   17898    |   27  | 36.3844131504 |
|   13132    |   3   | 24.7189218799 |
|   16261    |   98  | 64.4801045306 |
|   16619    |   14  | 26.3791012842 |
+------------+-------+---------------+
[4340 rows x 3 columns]
Note: Only the head of the SFrame is printed.
You can use print_rows(num_rows=m, num_columns=n) to print more rows and columns., 'rmse_by_item': Columns:
	Items	str
	count	int
	rmse	float

Rows: 5732

Data:
+--------------------------------+-------+---------------+
|             Items              | count |      rmse     |

In [18]:
#Get recommendations for first 5 users and print them
#users = range(1,6) specifies user ID of first 5 users
#k=5 specifies top 5 recommendations to be given
recommendereval = recommender.recommend(users=range(1,6),k=5)
recommendereval.print_rows(num_rows=25)

factorizationeval = factorization.recommend(users=range(1,6),k=5)
factorizationeval.print_rows(num_rows=25)

rfactorizationeval = rfactorization.recommend(users=range(1,6),k=5)
rfactorizationeval.print_rows(num_rows=25)

popularityeval = popularity.recommend(users=range(1,6),k=5)
popularityeval.print_rows(num_rows=25)

itemsimilarityeval = itemsimilarity.recommend(users=range(1,6),k=5)
itemsimilarityeval.print_rows(num_rows=25)

+------------+--------------------------------+---------------+------+
| CustomerID |             Items              |     score     | rank |
+------------+--------------------------------+---------------+------+
|     1      | 85099B:JUMBO BAG RED RETROSPOT | 21.8789995868 |  1   |
|     1      | 85123A:WHITE HANGING HEART...  | 21.4427095611 |  2   |
|     1      | 20725:LUNCH BAG RED RETROSPOT  | 21.4035172422 |  3   |
|     1      | 21212:PACK OF 72 RETROSPOT...  | 20.9827023704 |  4   |
|     1      | 84879:ASSORTED COLOUR BIRD...  | 20.9639593323 |  5   |
|     2      | 85099B:JUMBO BAG RED RETROSPOT | 21.8789995868 |  1   |
|     2      | 85123A:WHITE HANGING HEART...  | 21.4427095611 |  2   |
|     2      | 20725:LUNCH BAG RED RETROSPOT  | 21.4035172422 |  3   |
|     2      | 21212:PACK OF 72 RETROSPOT...  | 20.9827023704 |  4   |
|     2      | 84879:ASSORTED COLOUR BIRD...  | 20.9639593323 |  5   |
|     3      | 85099B:JUMBO BAG RED RETROSPOT | 21.8789995868 |  1   |
|     

In [19]:
model_compare= gl.compare(test, [recommender, factorization,rfactorization,popularity,itemsimilarity])

PROGRESS: Evaluate model M0

Precision and recall summary statistics by cutoff
+--------+-----------------+------------------+
| cutoff |  mean_precision |   mean_recall    |
+--------+-----------------+------------------+
|   1    | 0.0407288317256 | 0.00626235119341 |
|   2    | 0.0230439442658 | 0.00696830899056 |
|   3    | 0.0182207931404 | 0.00748667504751 |
|   4    | 0.0158092175777 | 0.00790164178374 |
|   5    | 0.0165058949625 | 0.00970273716239 |
|   6    |  0.016077170418 | 0.0109203554181  |
|   7    | 0.0148522431481 |  0.011637261675  |
|   8    | 0.0132636655949 |  0.012050943253  |
|   9    | 0.0125044658807 | 0.0123052504011  |
|   10   | 0.0113612004287 | 0.0126625208548  |
+--------+-----------------+------------------+
[10 rows x 3 columns]

PROGRESS: Evaluate model M1

Precision and recall summary statistics by cutoff
+--------+-------------------+-------------------+
| cutoff |   mean_precision  |    mean_recall    |
+--------+-------------------+---------------

In [20]:
gl.show_comparison(model_compare,[recommender, factorization,rfactorization,popularity,itemsimilarity])

In [21]:
view1= recommender.views.evaluate(test, baseline= rfactorization)
view1.show()

View object

URI: 		http://localhost:32212/view/15409bde-e166-4305-b570-fc8c83485a26
HTML: 		
<gl-recommender-evaluate
    uri="http://localhost:32212/view/8a87a9df-bb2a-4bfb-b861-87cc2f6737c3"
    api_key=""
/>
        

In [22]:
view2= rfactorization.views.evaluate(test, baseline= recommender)
view2.show()

View object

URI: 		http://localhost:32212/view/93e7c0c1-5987-4152-99b5-0d63e1c11198
HTML: 		
<gl-recommender-evaluate
    uri="http://localhost:32212/view/25b0bb31-05aa-4347-8d09-b1a48bc9c0a7"
    api_key=""
/>
        

In [23]:
high_rated_data = data[data["meanquantity"] >= 1]
low_rated_data = data[data["meanquantity"]  < 1]
train_data_2, test1 = gl.recommender.util.random_split_by_user(
                                    high_rated_data, user_id='CustomerID', item_id='Items')
train1 = train_data_2.append(low_rated_data)

In [24]:
recommender_im = gl.recommender.create(train1, user_id='CustomerID', item_id='Items', target='meanquantity')

factorization_im = gl.recommender.factorization_recommender.create(train1,user_id='CustomerID',item_id='Items',target='meanquantity', solver='als')

rfactorization_im= gl.recommender.ranking_factorization_recommender.create(train1,target='meanquantity', user_id='CustomerID',item_id='Items')

popularity_im=gl.recommender.popularity_recommender.create(train1,user_id='CustomerID',item_id='Items',target='meanquantity')

itemsimilarity_im=gl.recommender.item_similarity_recommender.create(train1,user_id='CustomerID',item_id='Items',target='meanquantity',similarity_type='pearson')

Recsys training: model = ranking_factorization_recommender

Preparing data set.

Data has 261464 observations with 4339 users and 5725 items.

Data prepared in: 0.339924s

Training ranking_factorization_recommender for recommendations.

...

| 1.34s                               | 100              | 5725            |

+-------------------------------------+------------------+-----------------+

Finalizing lookup tables.

Generating candidate set for working with new users.

Finished training in 1.36106s

In [25]:
print('recommender_im rmse=',recommender_im.evaluate_rmse(dataset=data,target='meanquantity'))

print('factorization_im rmse=',factorization_im.evaluate_rmse(dataset=data,target='meanquantity'))

print('rfactorization_im rmse=',rfactorization_im.evaluate_rmse(dataset=data,target='meanquantity'))

print('popularity_im rmse=',popularity_im.evaluate_rmse(dataset=data,target='meanquantity'))

print('item_similarity_im rmse=',itemsimilarity_im.evaluate_rmse(dataset=data,target='meanquantity'))

('recommender_im rmse=', {'rmse_by_user': Columns:
	CustomerID	int
	count	int
	rmse	float

Rows: 4340

Data:
+------------+-------+---------------+
| CustomerID | count |      rmse     |
+------------+-------+---------------+
|   14515    |   69  | 12.1944892963 |
|   14406    |   8   | 9.39948946376 |
|   17338    |  390  | 17.2927492662 |
|   15615    |  187  | 8.29987509271 |
|   17325    |   6   | 1.55233390428 |
|   16284    |   87  | 13.1616230907 |
|   17898    |   27  | 12.7675731307 |
|   13132    |   3   | 4.49979875401 |
|   16261    |   98  | 11.5720713308 |
|   16619    |   14  | 6.60680236239 |
+------------+-------+---------------+
[4340 rows x 3 columns]
Note: Only the head of the SFrame is printed.
You can use print_rows(num_rows=m, num_columns=n) to print more rows and columns., 'rmse_by_item': Columns:
	Items	str
	count	int
	rmse	float

Rows: 5732

Data:
+--------------------------------+-------+---------------+
|             Items              | count |      rmse   

In [26]:
#Get recommendations for first 5 users and print them
#users = range(1,6) specifies user ID of first 5 users
#k=5 specifies top 5 recommendations to be given
recommenderevalim = recommender_im.recommend(users=range(1,6),k=5)
recommenderevalim.print_rows(num_rows=25)

factorizationevalim = factorization_im.recommend(users=range(1,6),k=5)
factorizationevalim.print_rows(num_rows=25)

rfactorizationevalim = rfactorization_im.recommend(users=range(1,6),k=5)
rfactorizationevalim.print_rows(num_rows=25)

popularityevalim = popularity_im.recommend(users=range(1,6),k=5)
popularityevalim.print_rows(num_rows=25)

itemsimilarityevalim = itemsimilarity_im.recommend(users=range(1,6),k=5)
itemsimilarityevalim.print_rows(num_rows=25)

+------------+-------------------------------+---------------+------+
| CustomerID |             Items             |     score     | rank |
+------------+-------------------------------+---------------+------+
|     1      | 84077:WORLD WAR 2 GLIDERS ... | 11.7521383506 |  1   |
|     1      | 21212:PACK OF 72 RETROSPOT... | 11.2355963033 |  2   |
|     1      | 90214U:LETTER "U" BLING KE... | 11.1877428633 |  3   |
|     1      | 90021:LASER CUT MULTI STRA... | 11.1877428633 |  4   |
|     1      | 22145:CHRISTMAS CRAFT HEAR... | 11.1877428633 |  5   |
|     2      | 84077:WORLD WAR 2 GLIDERS ... | 11.7521383506 |  1   |
|     2      | 21212:PACK OF 72 RETROSPOT... | 11.2355963033 |  2   |
|     2      | 90214U:LETTER "U" BLING KE... | 11.1877428633 |  3   |
|     2      | 90021:LASER CUT MULTI STRA... | 11.1877428633 |  4   |
|     2      | 22145:CHRISTMAS CRAFT HEAR... | 11.1877428633 |  5   |
|     3      | 84077:WORLD WAR 2 GLIDERS ... | 11.7521383506 |  1   |
|     3      | 21212

In [27]:
model_compare_im= gl.compare(test1, [recommender_im, factorization_im,rfactorization_im,popularity_im,itemsimilarity_im])

PROGRESS: Evaluate model M0

Precision and recall summary statistics by cutoff
+--------+-------------------+-------------------+
| cutoff |   mean_precision  |    mean_recall    |
+--------+-------------------+-------------------+
|   1    |  0.00106157112527 |  3.0330603579e-06 |
|   2    |  0.00106157112527 | 6.20092339838e-05 |
|   3    |  0.00070771408351 | 6.20092339838e-05 |
|   4    | 0.000530785562633 | 6.20092339838e-05 |
|   5    | 0.000636942675159 |  0.00112358035925 |
|   6    |  0.00070771408351 |  0.0011994068682  |
|   7    | 0.000758265089475 |  0.00123157569017 |
|   8    |  0.00119426751592 |  0.00165178092726 |
|   9    |  0.00117952347252 |  0.00168969418173 |
|   10   |  0.00116772823779 |  0.00174556634622 |
+--------+-------------------+-------------------+
[10 rows x 3 columns]

PROGRESS: Evaluate model M1

Precision and recall summary statistics by cutoff
+--------+-------------------+------------------+
| cutoff |   mean_precision  |   mean_recall    |
+----

In [28]:
gl.show_comparison(model_compare_im,[recommender_im, factorization_im,rfactorization_im,popularity_im,itemsimilarity_im])

In [29]:
view3= recommender_im.views.evaluate(test1, baseline=rfactorization_im)
view3.show()

View object

URI: 		http://localhost:32212/view/a29b174f-fd71-4816-ab8e-ba13706700d5
HTML: 		
<gl-recommender-evaluate
    uri="http://localhost:32212/view/2ee54538-c727-414b-a045-337c84bfa1c1"
    api_key=""
/>
        

In [30]:
view4= rfactorization_im.views.evaluate(test1, baseline=recommender_im)
view4.show()

View object

URI: 		http://localhost:32212/view/bfd835e5-e150-4309-a578-d0c5bd7efe1d
HTML: 		
<gl-recommender-evaluate
    uri="http://localhost:32212/view/40afc9ac-77bc-47c6-83b1-cde52f0f98cd"
    api_key=""
/>
        

In [31]:
high_rated_data = data[data["stdquantity"] >= 1]
low_rated_data = data[data["stdquantity"] < 1]
train_data_3, test2 = gl.recommender.util.random_split_by_user(
                                    high_rated_data, user_id='CustomerID', item_id='Items')
train2 = train_data_3.append(low_rated_data)

In [32]:
recommender_is = gl.recommender.create(train1, user_id='CustomerID', item_id='Items', target='stdquantity')

factorization_is = gl.recommender.factorization_recommender.create(train1,user_id='CustomerID',item_id='Items',target='stdquantity',solver='als')

rfactorization_is= gl.recommender.ranking_factorization_recommender.create(train1,target='stdquantity',user_id='CustomerID',item_id='Items')

popularity_is=gl.recommender.popularity_recommender.create(train1,user_id='CustomerID',item_id='Items',target='stdquantity')

itemsimilarity_is=gl.recommender.item_similarity_recommender.create(train1,user_id='CustomerID',item_id='Items',target='stdquantity', similarity_type='pearson')

Recsys training: model = ranking_factorization_recommender

Preparing data set.

Data has 261464 observations with 4339 users and 5725 items.

Data prepared in: 0.289263s

Training ranking_factorization_recommender for recommendations.

...

| 1.24s                               | 100              | 5725            |

+-------------------------------------+------------------+-----------------+

Finalizing lookup tables.

Generating candidate set for working with new users.

Finished training in 1.25445s

In [33]:
print('recommender_is rmse=', recommender_is.evaluate_rmse(dataset=data,target='stdquantity'))

print('factorization_is rmse=', factorization_is.evaluate_rmse(dataset=data,target='stdquantity'))

print('rfactorization_is rmse=', rfactorization_is.evaluate_rmse(dataset=data,target='stdquantity'))

print('popularity_is rmse=',popularity_is.evaluate_rmse(dataset=data,target='stdquantity'))

print('item_similarity_is rmse=',itemsimilarity_is.evaluate_rmse(dataset=data,target='stdquantity'))

('recommender_is rmse=', {'rmse_by_user': Columns:
	CustomerID	int
	count	int
	rmse	float

Rows: 4340

Data:
+------------+-------+---------------+
| CustomerID | count |      rmse     |
+------------+-------+---------------+
|   14515    |   69  | 5.05254817693 |
|   14406    |   8   | 1.02400896061 |
|   17338    |  390  | 1.21708562324 |
|   15615    |  187  |  3.0796837078 |
|   17325    |   6   | 1.02459137322 |
|   16284    |   87  | 1.11773048814 |
|   17898    |   27  | 1.02335584293 |
|   13132    |   3   |  1.0275696037 |
|   16261    |   98  | 1.01446934291 |
|   16619    |   14  | 1.02218637464 |
+------------+-------+---------------+
[4340 rows x 3 columns]
Note: Only the head of the SFrame is printed.
You can use print_rows(num_rows=m, num_columns=n) to print more rows and columns., 'rmse_by_item': Columns:
	Items	str
	count	int
	rmse	float

Rows: 5732

Data:
+--------------------------------+-------+---------------+
|             Items              | count |      rmse   

In [34]:
#Get recommendations for first 5 users and print them
#users = range(1,6) specifies user ID of first 5 users
#k=5 specifies top 5 recommendations to be given
recommenderevalis = recommender_is.recommend(users=range(1,6),k=5)
recommenderevalis.print_rows(num_rows=25)

factorizationevalis = factorization_is.recommend(users=range(1,6),k=5)
factorizationevalis.print_rows(num_rows=25)

rfactorizationevalis = rfactorization_is.recommend(users=range(1,6),k=5)
rfactorizationevalis.print_rows(num_rows=25)

popularityevalis = popularity_is.recommend(users=range(1,6),k=5)
popularityevalis.print_rows(num_rows=25)

itemsimilarityevalis = itemsimilarity_is.recommend(users=range(1,6),k=5)
itemsimilarityevalis.print_rows(num_rows=25)

+------------+--------------------------------+---------------+------+
| CustomerID |             Items              |     score     | rank |
+------------+--------------------------------+---------------+------+
|     1      |    23084:RABBIT NIGHT LIGHT    | 1.04399874283 |  1   |
|     1      | 84879:ASSORTED COLOUR BIRD...  | 1.04296186299 |  2   |
|     1      | 85099B:JUMBO BAG RED RETROSPOT | 1.04215733684 |  3   |
|     1      | 15036:ASSORTED COLOURS SIL...  | 1.04080990132 |  4   |
|     1      | 22178:VICTORIAN GLASS HANG...  | 1.04076961306 |  5   |
|     2      |    23084:RABBIT NIGHT LIGHT    | 1.04399874283 |  1   |
|     2      | 84879:ASSORTED COLOUR BIRD...  | 1.04296186299 |  2   |
|     2      | 85099B:JUMBO BAG RED RETROSPOT | 1.04215733684 |  3   |
|     2      | 15036:ASSORTED COLOURS SIL...  | 1.04080990132 |  4   |
|     2      | 22178:VICTORIAN GLASS HANG...  | 1.04076961306 |  5   |
|     3      |    23084:RABBIT NIGHT LIGHT    | 1.04399874283 |  1   |
|     

In [35]:
model_compare_is= gl.compare(test2, [recommender_is, factorization_is,rfactorization_is,popularity_is,itemsimilarity_is])

PROGRESS: Evaluate model M0

Precision and recall summary statistics by cutoff
+--------+-------------------+------------------+
| cutoff |   mean_precision  |   mean_recall    |
+--------+-------------------+------------------+
|   1    |        0.0        |       0.0        |
|   2    | 0.000809061488673 | 0.00161812297735 |
|   3    | 0.000539374325782 | 0.00161812297735 |
|   4    | 0.000404530744337 | 0.00161812297735 |
|   5    | 0.000323624595469 | 0.00161812297735 |
|   6    | 0.000269687162891 | 0.00161812297735 |
|   7    | 0.000231160425335 | 0.00161812297735 |
|   8    | 0.000202265372168 | 0.00161812297735 |
|   9    | 0.000179791441927 | 0.00161812297735 |
|   10   | 0.000161812297735 | 0.00161812297735 |
+--------+-------------------+------------------+
[10 rows x 3 columns]

PROGRESS: Evaluate model M1

Precision and recall summary statistics by cutoff
+--------+----------------+-------------+
| cutoff | mean_precision | mean_recall |
+--------+----------------+--------

In [36]:
gl.show_comparison(model_compare_is,[recommender_is, factorization_is,rfactorization_is,popularity_is,itemsimilarity_is])

In [37]:
view5= recommender_is.views.evaluate(test2, baseline=rfactorization_is)
view5.show()

View object

URI: 		http://localhost:32212/view/293c0b57-dc65-4d3f-b88d-63a3fed47635
HTML: 		
<gl-recommender-evaluate
    uri="http://localhost:32212/view/566a6314-e712-4b57-8495-59cb792a17b7"
    api_key=""
/>
        

In [38]:
view6= rfactorization_is.views.evaluate(test2, baseline=recommender_is)
view6.show()

View object

URI: 		http://localhost:32212/view/904905e4-79c6-43ec-973f-484545dc6d4f
HTML: 		
<gl-recommender-evaluate
    uri="http://localhost:32212/view/a76833f2-7429-4149-be6d-2aa01b1013fe"
    api_key=""
/>
        